In [ ]:
%pip install -r requirements.txt

In [5]:
import gemini as gemini
import config as config
import bq as bq
import gcs as gcs
import utils as utils

import video_intelligence as gvi
from google.cloud import videointelligence_v1 as vi


config.WORKING_BUCKET =  "video-working-bucket-4293"
config.OUTPUT_BUCKET = "video-working-bucket-4293"
config.INPUT_BUCKET = "video-input-bucket-4293"
config.PROJECT_ID = "media-414316"
config.BQ_DATASET = "video_analytics_4293"
config.BQ_TABLE_GEMINI_RESULT = "video_analytics_4293.dev_test"

bucket =config.OUTPUT_BUCKET
import json
import pandas as pd


# Video intelligence API

In [2]:
from google.cloud import videointelligence_v1 as vi


In [ ]:
# Shot change
file = "fr-FR/SHOT_CHANGE_DETECTION/fr-FR_test1 - BEST UPCOMING MOVIES 2024 (Trailers) - 1710353080.1849315.json"

bucket = "video-working-bucket-4293"
data = gcs.read_json_from_gcs(bucket, file)

print(data)
annotation = vi.AnnotateVideoResponse(data)

gvi.splitVideo(data)


def split_video_shots_time_min(input_video, shots, min_shot_time):
    print(f"Start split video shots {input_video}")
    print(shots)
    if len(shots) == 0:
        print(f"No video shots found in {input_video}")
        return
    

    print(f" Video shots: {len(shots)} ".center(40, "-"))
    
    index = 0
    extend_chunk = False
    for i, shot in enumerate(shots):
        print(f"DEBUG - shot {i}")
        #print(shot)

        if extend_chunk == False:
            t1 = shot.start_time_offset.total_seconds()

        t2 = shot.end_time_offset.total_seconds()
        print(f"shot index : {i+1:>3} | video index {index} | {t1:7.3f} | {t2:7.3f}")


        output_video = f"{input_video } - {index} - {t1} - {t2}.mp4"
        
        if (t2 -t1) > min_shot_time:
            extend_chunk = False
            index = index+1

            print(f"input_video={input_video}, output_video={output_video}, start={t1}, end={t2}")

            #split_video(input_video=input_video, output_video=output_video, start=t1, end=t2)
            #yield output_video, t1, t2
        else:
            print(f"SKIP - input_video={input_video}, output_video={output_video}, start={t1}, end={t2}")
            extend_chunk = True


for annotation_result in annotation.annotation_results:
    # ex: input_bucket     "input_uri": "/video-input-bucket-2f60/fr-FR/cdanslair.mp4",
    index = 0

    print(f"Finished processing input: {annotation_result.input_uri}" ) 
    uri  = "gs:/"+annotation_result.input_uri
    
    print(f"full uri = {uri}")
    # gs://video-input-bucket-2f60/fr-FR/cdanslair.mp4

    bucketname, video_blobname = gcs.split_gcs_uri(uri)
    print(f"bucketname = {bucketname} - blobname = {video_blobname}")
    # video-input-bucket-2f60  /fr-FR/cdanslair.mp4
    localfile = video_blobname.replace("/", "_") # -{index}
    print(f"localfile = {localfile}")
    # fr-FR_cdanslair.mp4

    video_input = gcs.store_temp_video_from_gcs(bucketname, video_blobname, localfile= localfile)
    
    print(f"video_input = {video_input}")

    # if len(annotation_result.explicit_annotation.frames) > 0:# is not None:
    #     print("processing explicit_annotation")
    #     process_shots(annotation_result.explicit_annotation.frames, index, uri, video_blobname, video_input)
    
    if len(annotation_result.shot_annotations) > 0:# is not None:
        print("processing shot_annotations")
        split_video_shots_time_min(file, annotation_result.shot_annotations, 5)
  


In [ ]:
# Explicit content
file = "fr-FR/EXPLICIT_CONTENT_DETECTION/test1 - BEST UPCOMING MOVIES 2024 (Trailers) - 1709023409.1792483.json"
data = gcs.read_json_from_gcs(bucket, file)

print(data)
annotation = vi.AnnotateVideoResponse(data)

#gvi.splitVideo(data)
gvi.storeVideoIntelligenceData(data)

In [ ]:
# TEXT DETECTION
file = "fr-FR/TEXT_DETECTION/test1 - BEST UPCOMING MOVIES 2024 (Trailers) - 1709023409.2954755.json"

data = gcs.read_json_from_gcs(bucket, file)
annotation = vi.AnnotateVideoResponse(data)

#gvi.splitVideo(data)
gvi.storeVideoIntelligenceData(data)

## Video Edit

In [ ]:
import videoedit as videoedit
local_file = "/Users/julienmiquel/Downloads/fr-FR_test1 - BEST UPCOMING MOVIES 2024 (Trailers).mp4"
videoedit.split_video_shots_time_min(local_file, )

# Gemini

In [16]:
import gemini as gemini
import config as config
import bq as bq
import gcs as gcs
import utils as utils

import video_intelligence as gvi
from google.cloud import videointelligence_v1 as vi


config.WORKING_BUCKET =  "video-working-bucket-4293"
config.OUTPUT_BUCKET = "video-working-bucket-4293"
config.INPUT_BUCKET = "video-input-bucket-4293"
config.PROJECT_ID = "media-414316"
config.BQ_DATASET = "video_analytics_4293"
config.BQ_TABLE_GEMINI_RESULT = "video_analytics_4293.dev_test"

config.REGION = "europe-west4"
config.REGIONS = ["europe-west4", "europe-west1", "us-central1"]

bucket =config.OUTPUT_BUCKET



import json
import pandas as pd


uri = "gs://video-output-bucket-4293/CSA/TEST/CSA_3_23941614_0_1500kbps_20240311.mp4_chunks - 6 - 7.92 - 9.8.mp4"
name = "CSA/TEST/CSA_3_23941614_0_1500kbps_20240311.mp4_chunks - 6 - 7.92 - 9.8.mp4"

prompt =    """Classification task. Choose between PEGI rating from (3, 7, 12, 16, 18). Based on the following content rate the intensity of the scene from: 
PEGI 3 The content of video with a PEGI 3 rating is considered suitable for all age groups. The video should not contain any sounds or pictures that are likely to frighten young children. A very mild form of violence (in a comical context or a childlike setting) is acceptable. No bad language should be heard. 

PEGI 7 video content with scenes or sounds that can possibly frightening to younger children should fall in this category. Very mild forms of violence (implied, non-detailed, or non-realistic violence) are acceptable for a video with a PEGI 7 rating 

PEGI 12 Video that show violence of a slightly more graphic nature towards fantasy characters or nonrealistic violence towards human-like characters would fall in this age category. Sexual innuendo or sexual posturing can be present, while any bad language in this category must be mild. Gambling as it is normally carried out in real life in casinos or gambling halls can also be present.

PEGI 16 This rating is applied once the depiction of violence (or sexual activity) reaches a stage that looks the same as would be expected in real life. The use of bad language in video with a PEGI 16 rating can be more extreme, while video of chance, and the use of tobacco, alcohol or illegal drugs can also be present. 

PEGI 18 is rating for adult content.

CONTENT TO RATE: 
"""

prompt =    """what do you see in each part of this video ?
Describe in detail each part of the video.

VIDEO: 
"""

# prompt =    """Describe violence in detail present in the video.
# If no violence is present. Answer "nice video"
# VIDEO: 
# """

res = gemini.content_moderation_gemini(uri, prompt=prompt)
print(f"moderation content done on chunck uri {uri} with res = {res}")
# print(80*"*")
# print(res)
# print(80*"*")

# print("save json result in output bucket")
# json_file_path = gcs.write_text_to_gcs(config.OUTPUT_BUCKET, utils.replace_extension(name, ".json"), res, "text/json")
# print(f"json_file_path = {json_file_path}")

# # dict= json.loads(res)
# # dict= dict["csa_rules"]

# print("read tags from source uri")
# bucketname, video_blobname = gcs.split_gcs_uri(uri)
# tags = gcs.read_tags_from_gcs(bucketname, video_blobname)

# if tags is None:
#     print("no tags found. WARNING do not save.")
# else:
#     print(f"uri= {uri} - tags = {tags}")
#     dict.update(tags)     
#     tags["description"]       = res
#     # generate time
#     tags["update_time"]       = utils.get_date_time_string()

#     tags["uri"] = uri
#     df = pd.DataFrame([tags])

#     print(df.to_json())
#     bq.save_bq(df,config.BQ_TABLE_GEMINI_RESULT, project_id=config.PROJECT_ID )

# df

content_moderation_gemini gs://video-output-bucket-4293/CSA/fr-FR/fr-FR_test1 - BEST UPCOMING MOVIES 2024 (Trailers).mp4/chunks - 1 - 0.0 - 5.566666.mp4
Create videoPArt
file_data {
  mime_type: "video/mp4"
  file_uri: "gs://video-output-bucket-4293/CSA/fr-FR/fr-FR_test1 - BEST UPCOMING MOVIES 2024 (Trailers).mp4/chunks - 1 - 0.0 - 5.566666.mp4"
}

vertexai init project=media-414316, location=europe-west4
moderation content done on chunck uri gs://video-output-bucket-4293/CSA/fr-FR/fr-FR_test1 - BEST UPCOMING MOVIES 2024 (Trailers).mp4/chunks - 1 - 0.0 - 5.566666.mp4 with res =  Part 1: A gorilla charges toward the camera

Part 2: A woman runs through a grassy field

Part 3: A dog runs through a grassy field

Part 4: People run from an explosion in a city

Part 5: A man in a yellow jacket is attacked by a monster

Part 6: Deadpool fights an enemy

Part 7: Deadpool shoots two guns at the camera


In [ ]:
import base64
import vertexai
from vertexai.generative_models import GenerativeModel, Part
import vertexai.generative_models as generative_models

def generate(video_input):
    print(f"content_moderation_gemini {video_input}")
    if type(video_input) == str:
        video_input = Part.from_uri(uri=video_input, mime_type="video/mp4")

    elif type(input) == 'Part':
        video_input = video_input
    else:
        print(f"input is not supported: {video_input}")
        return 
    vertexai.init(project="media-414316", location="europe-west1")
    model = GenerativeModel("gemini-1.0-pro-vision-001")
    responses = model.generate_content(
        ["""You are an expert in violence content moderation.
    Explain why you provide the rating with the content moderation rule and without offensive quote.

    You classify text with CSA rules. Answer short JSON results like an API without quote with the following format:
    {\"\\\"csa_rules\\\": {
        \\\"violence\\\": \"0\",
        \\\"violence_evidence\\\":  \\\"\\\"
    }

    Evaluate CSA rules based on this video part and output them in JSON. Return a valide JSON format.""", video_input, """JSON"""],
        generation_config={
            "max_output_tokens": 2048,
            "temperature": 0,
            "top_p": 1,
            "top_k": 40
        },
        safety_settings={
            generative_models.HarmCategory.HARM_CATEGORY_HATE_SPEECH: generative_models.HarmBlockThreshold.BLOCK_MEDIUM_AND_ABOVE,
            generative_models.HarmCategory.HARM_CATEGORY_DANGEROUS_CONTENT: generative_models.HarmBlockThreshold.BLOCK_MEDIUM_AND_ABOVE,
            generative_models.HarmCategory.HARM_CATEGORY_SEXUALLY_EXPLICIT: generative_models.HarmBlockThreshold.BLOCK_MEDIUM_AND_ABOVE,
            generative_models.HarmCategory.HARM_CATEGORY_HARASSMENT: generative_models.HarmBlockThreshold.BLOCK_MEDIUM_AND_ABOVE,
        },
        stream=True,
    )
  
        


    answer = []
    for response in responses:
        text = response.text
        print(text, end="")    
        answer.append(text)

    str_json = "".join(answer)
    #str_json = CleanJsonOutput(str_json)
    #print(str_json)

    return str_json
  
video_input = "gs://video-output-bucket-031f/CSA/fr-FR/Copy of fr-FR_test1 - BEST UPCOMING MOVIES 2024 (Trailers).mp4/chunks - 1 - 0.0 - 0.633333.mp4"

#video1 = Part.from_uri(uri=video_input, mime_type="video/mp4")
generate(video_input)

# Text processing

In [ ]:
%pip install jsonpath-ng

In [4]:
import json
from google.cloud import bigquery

# Replace with your project ID and BigQuery dataset/table names
PROJECT_ID = "media-414316"
DATASET = "video_analytics_031f"
TABLE = "results"


def bigquery_to_json(bigquery_results, video_source):
    annotation_results = []
    #shot_label_annotations = []

    last_end_time_offset = {
        "seconds": 0,
        "nanos": 0
    }
    segments = []
    
    result_item = {
        "input_uri": video_source,  
        "segment": {
            "start_time_offset": {
                "seconds": 0,
                "nanos": 0
                },
            "end_time_offset": last_end_time_offset
        },
        # "segment_label_annotations": [],
        "shot_label_annotations": []
    }
    annotation_results.append(result_item)

    for row in bigquery_results:
        description = get_description(row)
        if description: # and description:

            # Function to calculate time offsets based on your data
            start_time_offset, end_time_offset = calculate_time_offsets(row)

            segment_label = {
                "entity": {
                    "entity_id": "/m/00000",

                    # "language_code": "en-US"
                    "description": description
                },
                "segments": [{
                    "segment": {
                        "start_time_offset": start_time_offset,
                        "end_time_offset": end_time_offset
                    },
                    # Add 'confidence' if applicable
                    'confidence': 1.0
                }]
            }
            last_end_time_offset = end_time_offset
            
            segments.append(segment_label)
            
            result_item["shot_label_annotations"].append(segment_label)
            #shot_label_annotations.append(segment_label)

        #if len(result_item) > 0 and len(result_item["shot_label_annotations"]) > 0:
        annotation_results.append(result_item)

    #if len(annotation_results) > 0:
    annotation_results[0]['segment']['end_time_offset'] = last_end_time_offset
    

    return {"annotation_results": annotation_results}

# Example of how to calculate offsets (adjust to your data)


def calculate_time_offsets(row):
    start = float(row.get("time_start", "0"))  # Adjust field name if needed
    start_seconds, start_nanos = getSecondsNanos(start)

    end = float(row.get("time_stop", "0"))    # Adjust field name if needed
    end_seconds, end_nanos = getSecondsNanos(end)

    return {"seconds": start_seconds, "nanos": start_nanos}, {"seconds": end_seconds, "nanos": end_nanos}


def getSecondsNanos(start):
    start_seconds = int(start)
    start_nanos = int((start - start_seconds) * 10000000)
    return start_seconds, start_nanos


def get_description(row):
    description = row.get(f"description", "")
    index = row.get("index", "0")
    start = float(row.get("time_start", "0"))  # Adjust field name if needed
    end = float(row.get("time_stop", "0"))    # Adjust field name if needed

    if len(description) > 0:
        description = f"{index} ({start} - {end}) : {description}"
        print(description)
        return description
    else:
        return None


# BigQuery query execution
client = bigquery.Client(project=PROJECT_ID)
#filter = "gs://video-input-bucket-031f/fr-FR/House of the Dragon - Rhaenyra and Criston Cole sex scene.mp4"
filter = "gs://video-input-bucket-031f/fr-FR/BEST UPCOMING MOVIES  2024 (Trailers).mp4"

query = f"SELECT * FROM `{DATASET}.{TABLE}` where video_source = '{filter}'  order by  CAST(index AS INT64)  asc"
print(query)
query_job = client.query(query)
results = query_job.result()

# Conversion and output
json_data = bigquery_to_json(results, filter)
label_moderation = json.dumps(json_data, indent=2)
print(label_moderation)

# write file with content label_moderation

with open('label_moderation_Trailers.json', 'w') as f:
    f.write(label_moderation)

SELECT * FROM `video_analytics_031f.results` where video_source = 'gs://video-input-bucket-031f/fr-FR/BEST UPCOMING MOVIES  2024 (Trailers).mp4'  order by  CAST(index AS INT64)  asc
1 (0.0 - 0.633333) :  The video contains a gorilla that is roaring and showing its teeth. The gorilla is also running towards the camera. This could be considered to be quite intense for younger children, so I would rate this video as PEGI 7.
2 (0.666666 - 1.833333) :  The content of the video is a horse race. There is no violence, no bad language, no sexual content, and no gambling. The video is suitable for all age groups. The PEGI rating for this video is 3.
3 (1.866666 - 3.4) :  based on the content of the video, the appropriate PEGI rating would be 18. The video contains graphic violence and disturbing imagery that is not suitable for children or young adults.
4 (3.433333 - 5.566666) :  The video contains violence, blood, and gore. It is rated R for violence and language.
5 (5.6 - 6.066666) :  The vide

In [6]:
!pip install ipywidgets

   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 139.4/139.4 kB 5.4 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 215.0/215.0 kB 8.6 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 2.3/2.3 MB 7.1 MB/s eta 0:00:00a 0:00:01m
DEPRECATION: textract 1.6.5 has a non-standard dependency specifier extract-msg<=0.29.*. pip 24.1 will enforce this behaviour change. A possible replacement is to upgrade to a newer version of textract or contact the author to suggest that they release a version with a conforming dependency specifiers. Discussion can be found at https://github.com/pypa/pip/issues/12063


In [19]:
%load_ext google.cloud.bigquery


In [2]:
%%bigquery df

with prediction as (
SELECT
  ml_generate_text_result['predictions'][0]['content'] AS generated_text,
  ml_generate_text_result['predictions'][0]['safetyAttributes']
    AS safety_attributes,
    
  * EXCEPT (ml_generate_text_result)
FROM
  ML.GENERATE_TEXT(
    MODEL `media-414316.video_analytics_031f.llm_model`,
    (
      SELECT
        CONCAT("Summarize with hashtags:"
        , description ) AS prompt,
        *
      FROM
        `media-414316.video_analytics_031f.results` 
      LIMIT 5
    ),
    STRUCT(
      0. AS temperature,
      100 AS max_output_tokens,
      10 AS top_k,
      1.0 AS top_p
      
      ))

)
select replace(string(generated_text), "```", "") AS generated_text, description from prediction

Query is running:   0%|          |

Downloading:   0%|          |

In [2]:
df

NameError: name 'df' is not defined

In [ ]:



with prediction as (
SELECT
  ml_generate_text_result['predictions'][0]['content'] AS generated_text,
  ml_generate_text_result['predictions'][0]['safetyAttributes']
    AS safety_attributes,
  * EXCEPT (ml_generate_text_result)
FROM
  ML.GENERATE_TEXT(
    MODEL `media-414316.video_analytics_031f.llm_model`,
    (
      SELECT
        CONCAT("Extract PEGI category and evidence. Answer in json format like an API call. Reply with valid JSON.",
        "Exemple:",
        "",
        ""
        , description,
"""  ```json\n""" ) AS prompt,
        *
      FROM
        `media-414316.video_analytics_031f.results` 
      LIMIT 5
    ),
    STRUCT(
      0. AS temperature,
      100 AS max_output_tokens,
      10 AS top_k,
      1.0 AS top_p
      
      ))

)
select replace(string(generated_text), "```", "") AS generated_text from prediction

In [ ]:



with prediction as (
SELECT
  ml_generate_text_result['predictions'][0]['content'] AS generated_text,
  ml_generate_text_result['predictions'][0]['safetyAttributes']
    AS safety_attributes,
    description,
  * EXCEPT (ml_generate_text_result)
FROM
  ML.GENERATE_TEXT(
    MODEL `media-414316.video_analytics_031f.llm_model`,
    (
      SELECT
        CONCAT("Extract PEGI category and evidence. Answer in json format like an API call. Reply with valid JSON.",
        "Exemple:",
        "TEXT_TO_RATE:\n",
        "The video is about a girl who is being bullied. She is sitting alone in a room, looking sad and lonely. The video is very sad and moving, and it is clear that the girl is in a lot of pain. I would rate this video as PEGI 7, as it is not suitable for children under the age of 7.",
        "JSON_PEGI:",
        """ { \"PEGI\": 12, \"Evidence\": \"The video contains scenes of violence and gore that may be disturbing to younger viewers."
}"
        , description,
"""  ```json\n""" ) AS prompt,
        *
      FROM
        `media-414316.video_analytics_031f.results` 
      LIMIT 5
    ),
    STRUCT(
      0. AS temperature,
      100 AS max_output_tokens,
      10 AS top_k,
      1.0 AS top_p
      
      ))

)
select replace(string(generated_text), "```", "") AS JSON,  * from prediction

In [ ]:
SELECT * FROM `video_analytics_031f.results`  where violence!='0' 
#and video_source = 'gs://video-input-bucket-031f/fr-FR/fr-FR_test1 - BEST UPCOMING MOVIES 2024 (Trailers).mp4' order by  CAST(index AS INT64)  asc


In [ ]:
SELECT * FROM `video_analytics_031f.results` where video_source = 'gs://video-input-bucket-031f/fr-FR/BEST UPCOMING MOVIES  2024 (Trailers).mp4'

 order by  CAST(index AS INT64)  asc;

 SELECT index, count(*) FROM `video_analytics_031f.results` where video_source = 'gs://video-input-bucket-031f/fr-FR/BEST UPCOMING MOVIES  2024 (Trailers).mp4'
 group by index
 order by  CAST(index AS INT64)  asc;



In [ ]:
SELECT * FROM `media-414316.video_analytics_031f.dev_test2` order by update_time desc

In [20]:
%%biquery



CREATE OR REPLACE MODEL `media-414316.video_analytics_4293.textbison1`
  REMOTE WITH CONNECTION `europe-west4.vertexai`
  OPTIONS (ENDPOINT = 'text-bison@001');


CREATE OR REPLACE MODEL `media-414316.video_analytics_4293.textbison2`
  REMOTE WITH CONNECTION `europe-west4.vertexai`
  OPTIONS (ENDPOINT = 'text-bison@002');








UsageError: Cell magic `%%biquery` not found.


In [ ]:
SELECT *
FROM
  ML.GENERATE_TEXT(
    MODEL `media-414316.video_analytics_031f.llm_model`,
    (SELECT 'What is the purpose of dreams?' AS prompt),
    STRUCT(
      0.8 AS temperature,
      1024 AS max_output_tokens,
      0.95 AS top_p,
      40 AS top_k));

In [ ]:
SELECT  count(*), video_source  FROM `video_analytics_031f.results` group by  video_source


In [2]:
def detect_web(path):
    """Detects web annotations given an image."""
    from google.cloud import vision

    client = vision.ImageAnnotatorClient()

    with open(path, "rb") as image_file:
         content = image_file.read()

    image = vision.Image(content=content)

    response = client.web_detection(image)
    annotations = response.web_detection

    if annotations.best_guess_labels:
        for label in annotations.best_guess_labels:
            print(f"\nBest guess label: {label.label}")

    if annotations.pages_with_matching_images:
        print(
            "\n{} Pages with matching images found:".format(
                len(annotations.pages_with_matching_images)
            )
        )

        for page in annotations.pages_with_matching_images:
            print(f"\n\tPage url   : {page.url}")

            if page.full_matching_images:
                print(
                    "\t{} Full Matches found: ".format(len(page.full_matching_images))
                )

                for image in page.full_matching_images:
                    print(f"\t\tImage url  : {image.url}")

            if page.partial_matching_images:
                print(
                    "\t{} Partial Matches found: ".format(
                        len(page.partial_matching_images)
                    )
                )

                for image in page.partial_matching_images:
                    print(f"\t\tImage url  : {image.url}")

    if annotations.web_entities:
        print("\n{} Web entities found: ".format(len(annotations.web_entities)))

        for entity in annotations.web_entities:
            print(f"\n\tScore      : {entity.score}")
            print(f"\tDescription: {entity.description}")

    if annotations.visually_similar_images:
        print(
            "\n{} visually similar images found:\n".format(
                len(annotations.visually_similar_images)
            )
        )

        for image in annotations.visually_similar_images:
            print(f"\tImage url    : {image.url}")

    if response.error.message:
        raise Exception(
            "{}\nFor more info on error messages, check: "
            "https://cloud.google.com/apis/design/errors".format(response.error.message)
        )


detect_web("https://static.orpi.com/images/sweepbright-s3/default/af91cb08-628e-4644-92df-6ce3078eb3c6--e72b2cdf-f690-48da-97f6-e8c350337ed2.jpg")

TypeError: ImageAnnotatorClient.web_detection() missing 1 required positional argument: 'image'

In [3]:
%pip install google-cloud-vision==3.4.2


DEPRECATION: textract 1.6.5 has a non-standard dependency specifier extract-msg<=0.29.*. pip 24.1 will enforce this behaviour change. A possible replacement is to upgrade to a newer version of textract or contact the author to suggest that they release a version with a conforming dependency specifiers. Discussion can be found at https://github.com/pypa/pip/issues/12063
Note: you may need to restart the kernel to use updated packages.


# Test cases

Rating différent suite à 2 appels

⇒ chunk à debuger 


Différence de rating en fonction de la qualité de la vidéo.

1500kbps 
10 Mbps

Quota



CF - Memoire / cpu

Changement de stratégie 
Chunk pas inférieur à 5s 




In [3]:
#1500kbps 

#10 Mbps

!gsutil cp ../../data/* gs://video-output-bucket-4293/CSA/TEST/

Copying file://../../data/CSA_3_23941614_0.mp4_chunks - 6 - 7.88 - 9.76.mp4 [Content-Type=video/mp4]...
Copying file://../../data/CSA_3_23941614_0_1500kbps_20240311.mp4_chunks - 1 - 0.04 - 1.92.mp4 [Content-Type=video/mp4]...
Copying file://../../data/CSA_3_23941614_0_1500kbps_20240311.mp4_chunks - 6 - 7.92 - 9.8.mp4 [Content-Type=video/mp4]...
Copying file://../../data/export_Gemini.xlsx [Content-Type=application/vnd.openxmlformats-officedocument.spreadsheetml.sheet]...
- [4 files][  2.1 MiB/  2.1 MiB]                                                
Operation completed over 4 objects/2.1 MiB.                                      


In [ ]:
gemini.content_moderation_gemini("")